<a href="https://colab.research.google.com/github/hsyoon99/MedQuad/blob/main/MedQuad1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/gdrive', force_remount=True)

Mounted at /gdrive


In [ ]:
import numpy as np

dataset = np.loadtxt("", delimiter=",")

print(dataset)

In [7]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
pip install customized_konlpy

     |████████████████████████████████| 890kB 18.5MB/s 
     |████████████████████████████████| 460kB 54.4MB/s 
     |████████████████████████████████| 19.4MB 163kB/s 
     |████████████████████████████████| 92kB 14.2MB/s 
  Found existing installation: tweepy 3.6.0
    Uninstalling tweepy-3.6.0:
      Successfully uninstalled tweepy-3.6.0
  Found existing installation: beautifulsoup4 4.6.3
    Uninstalling beautifulsoup4-4.6.3:
      Successfully uninstalled beautifulsoup4-4.6.3


In [66]:
from ckonlpy.tag import Twitter
from tensorflow.keras.utils import get_file
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
import numpy as np
from nltk import FreqDist
from functools import reduce
import os
import re
import matplotlib.pyplot as plt

In [67]:
TRAIN_FILE = os.path.join('/content/drive/MyDrive/hackathon_2-2/data/train/MedQuAD_v1.0_train.json')

In [68]:
#@title 기본 제목 텍스트
import json
from pprint import pprint

with open(TRAIN_FILE) as data_file:    
    data = json.load(data_file)

In [9]:
data["data"][0]

{'paragraphs': [{'context': 'A: 안녕하세요. A: 혹시 입원하러 오셨나요? B: 네. 여기요. A: 네. A: 000님 기다리고 있었어요. A: 얼른 키와 몸무게부터 재고 병실 안내해드리겠습니다. B: 네. A: 여기 올라가 보시겠어요? B: 짐은. A: 아 짐은 옆 의자에 두시면 될것같아요. B: 네. A: 네 되셨습니다. A: 내려오세요. B: 네. A: 그러면 이제 병실 안내해드릴건데 그전에 환자팔찌 채워드릴게요. A: 앞으로 주사나 약 투여할 때 꼭 확인해야하니까 빼거나 잃어 버리면 말씀해주세요. B: 네. A: 환자분 성함도 계속 물어볼텐데 정확한 환자 및 약물 투여를 확인하기 위해 하는 필요한 절차이니까 협조 잘 부탁드릴게요! B: 네네. A: 그러면 성함이랑 생년월일 말씀해주시겠어요? B: 네. 000, 00년 00월 00일. A: 네 000님 팔찌 매드릴게요. A: 되셨습니다. A: 병실 안내해드릴게요 이쪽으로 따라와 주세요. B: 네. A: 네 여기입니다. A: 어제 다 퇴원하셔서 지금은 자리가 다 비워져 있어요~ 편하신 자리에 앉아 주시겠어요? B: 네. 여기로 할게요. A: 네 나중에 자리 바꾸기 힘들다는 점 미리 말씀드리고요~ 일단은 환의로 갈아입으시고 짐 정리하고 계시면 다시와서 혈압이랑 체온도 재고, 환자분의 정확한 상태파악을 위해 몇가지 물어볼거에요. B: 네네. B: 이거는 제가 사용해도 되는거맞죠? A: 네네 열면 그냥 열릴꺼에요 편하게 사용하면 되세요. A: 지금 비밀번호가 초기화되서 샾버튼 누르시고 편하신 번호 4자리 입력하시면 되세요. B: 아 네. A: 네 그러면 이따가 다시 오겠습니다. A: 커튼 치고 갈게요. B: 네. A: 환자분~ B: 네. A: 옷 다 갈아입으셨으면 들어갈게요. B: 네. A: 그러면 이제 혈압부터 재겠습니다. A: 편하게 누워계셔도 되세요. A: 팔만 편하게 내려주세요. B: 네. A: 네 감사합니다. A: 혈압은 108에 68, 맥박은 94회이시네요. A: 체온은 정상이

In [ ]:
data["data"][0].keys()

dict_keys(['paragraphs', 'title'])

In [49]:
data["data"][334]

{'paragraphs': [{'context': 'A: 안녕하세요. A: 입원하러 오신 신짱구님 보호자분 맞으신가요? C: 네. A: 입원팔찌부터 매드릴게요, 혹시 아이 생년월일이 어떻게 되요? C: 2015년 5월 16일이요. A: 네 팔찌 매드릴건데 앞으로 정확한 환자 파악을 위해서 필요하니까 떄지거나 하면 말씀해주세요. C: 네… A: 일단 키와 몸무게부터 재고 병실로 안내해 드리도록 하겠습니다. A: 이쪽으로 올라와보실까요? C: 아이가 말하기 힘들어해요. A: 네 입원하는게 처음이고 하니까 더 불안해서 말이 잘 안나올꺼에요. A: 일부러 힘들게 말하지 않아도 되요, 이제 신발 신고 내려오고요, 병실로 안내해드리겠습니다. C: 네. A: 1인실이시고요, 먼저 가는길에 병동안내부터 하도록 하겠습니다. A: 간호사 병동입구를 기준으로 앞에는 배선실, 왼쪽 코너에는 화장실이 있어요. C: 병실에는 화장실이 없어요? C: 1인실인데? A: 병실에도 화장실이 있고요, 다른병실의 경우 4일실과 2인실도 있기 때문에 여기도 따로 마련해 놓은 겁니다. C: 네. A: 여기 배선실 안에는 전자레인지, Tv, 쇼파, 정수기 등 편하게 휴식실로 생각하시면 되시고요, 식사시간에는 여기 안에 식판대가 들어와있을거에요, 안에 넣어주시면 됩니다. C: 네. A: 그리고 배선실나와서 저기 보이는 유리문이 비상구고요, 반대편 복도에도 마찬가지로 비상구가 위치해있습니다. A: 중앙계단도 비상시 이용가능하지만 아무래도 사람이 몰릴걸 예상하기 때문에 양쪽의 비상구를 이용하시는 편이 나으실거에요, 비상시 안내에 따라서 이동해주시면 되시고요, 이제는 병실로 들어가겠습니다. C: 네. A: 아 환의갈아입고는 여기 문여시면 세탁망이 있어요, 여기에다 넣어주시면 됩니다, C: 네. A: 그러면 이제 간단한 병동 안내는 끝났고요, 병원 1층에는 00은행, 00은행ATM기기, 증명서발급기, 입원계, 퇴원계, 카페 및 편의점이 위치해 있고요, 2층에는 의료기상사, 각종 외래 등이 위치해 있습니다. A

In [13]:
data["data"][0]["paragraphs"]

[{'context': 'A: 안녕하세요. A: 혹시 입원하러 오셨나요? B: 네. 여기요. A: 네. A: 000님 기다리고 있었어요. A: 얼른 키와 몸무게부터 재고 병실 안내해드리겠습니다. B: 네. A: 여기 올라가 보시겠어요? B: 짐은. A: 아 짐은 옆 의자에 두시면 될것같아요. B: 네. A: 네 되셨습니다. A: 내려오세요. B: 네. A: 그러면 이제 병실 안내해드릴건데 그전에 환자팔찌 채워드릴게요. A: 앞으로 주사나 약 투여할 때 꼭 확인해야하니까 빼거나 잃어 버리면 말씀해주세요. B: 네. A: 환자분 성함도 계속 물어볼텐데 정확한 환자 및 약물 투여를 확인하기 위해 하는 필요한 절차이니까 협조 잘 부탁드릴게요! B: 네네. A: 그러면 성함이랑 생년월일 말씀해주시겠어요? B: 네. 000, 00년 00월 00일. A: 네 000님 팔찌 매드릴게요. A: 되셨습니다. A: 병실 안내해드릴게요 이쪽으로 따라와 주세요. B: 네. A: 네 여기입니다. A: 어제 다 퇴원하셔서 지금은 자리가 다 비워져 있어요~ 편하신 자리에 앉아 주시겠어요? B: 네. 여기로 할게요. A: 네 나중에 자리 바꾸기 힘들다는 점 미리 말씀드리고요~ 일단은 환의로 갈아입으시고 짐 정리하고 계시면 다시와서 혈압이랑 체온도 재고, 환자분의 정확한 상태파악을 위해 몇가지 물어볼거에요. B: 네네. B: 이거는 제가 사용해도 되는거맞죠? A: 네네 열면 그냥 열릴꺼에요 편하게 사용하면 되세요. A: 지금 비밀번호가 초기화되서 샾버튼 누르시고 편하신 번호 4자리 입력하시면 되세요. B: 아 네. A: 네 그러면 이따가 다시 오겠습니다. A: 커튼 치고 갈게요. B: 네. A: 환자분~ B: 네. A: 옷 다 갈아입으셨으면 들어갈게요. B: 네. A: 그러면 이제 혈압부터 재겠습니다. A: 편하게 누워계셔도 되세요. A: 팔만 편하게 내려주세요. B: 네. A: 네 감사합니다. A: 혈압은 108에 68, 맥박은 94회이시네요. A: 체온은 정상이에요. B: 몇도에요? A:

In [14]:
data["data"][0]["title"]

'./train/KMB_23_210115_H.txt'

In [52]:
data.keys()

dict_keys(['version', 'data'])

In [25]:
data.get("version")

'MedQuAD_v1.0_train'

In [26]:
data.get("data")

[{'paragraphs': [{'context': 'A: 안녕하세요. A: 혹시 입원하러 오셨나요? B: 네. 여기요. A: 네. A: 000님 기다리고 있었어요. A: 얼른 키와 몸무게부터 재고 병실 안내해드리겠습니다. B: 네. A: 여기 올라가 보시겠어요? B: 짐은. A: 아 짐은 옆 의자에 두시면 될것같아요. B: 네. A: 네 되셨습니다. A: 내려오세요. B: 네. A: 그러면 이제 병실 안내해드릴건데 그전에 환자팔찌 채워드릴게요. A: 앞으로 주사나 약 투여할 때 꼭 확인해야하니까 빼거나 잃어 버리면 말씀해주세요. B: 네. A: 환자분 성함도 계속 물어볼텐데 정확한 환자 및 약물 투여를 확인하기 위해 하는 필요한 절차이니까 협조 잘 부탁드릴게요! B: 네네. A: 그러면 성함이랑 생년월일 말씀해주시겠어요? B: 네. 000, 00년 00월 00일. A: 네 000님 팔찌 매드릴게요. A: 되셨습니다. A: 병실 안내해드릴게요 이쪽으로 따라와 주세요. B: 네. A: 네 여기입니다. A: 어제 다 퇴원하셔서 지금은 자리가 다 비워져 있어요~ 편하신 자리에 앉아 주시겠어요? B: 네. 여기로 할게요. A: 네 나중에 자리 바꾸기 힘들다는 점 미리 말씀드리고요~ 일단은 환의로 갈아입으시고 짐 정리하고 계시면 다시와서 혈압이랑 체온도 재고, 환자분의 정확한 상태파악을 위해 몇가지 물어볼거에요. B: 네네. B: 이거는 제가 사용해도 되는거맞죠? A: 네네 열면 그냥 열릴꺼에요 편하게 사용하면 되세요. A: 지금 비밀번호가 초기화되서 샾버튼 누르시고 편하신 번호 4자리 입력하시면 되세요. B: 아 네. A: 네 그러면 이따가 다시 오겠습니다. A: 커튼 치고 갈게요. B: 네. A: 환자분~ B: 네. A: 옷 다 갈아입으셨으면 들어갈게요. B: 네. A: 그러면 이제 혈압부터 재겠습니다. A: 편하게 누워계셔도 되세요. A: 팔만 편하게 내려주세요. B: 네. A: 네 감사합니다. A: 혈압은 108에 68, 맥박은 94회이시네요. A: 체온은 정상

In [32]:
values = data.values()

In [33]:
values

dict_values(['MedQuAD_v1.0_train', [{'paragraphs': [{'qas': [{'answers': [{'text': 'A: 최근 삼 개월 이내에 입원이나 수술하신 적 있으신가요? B: 아니요.', 'answer_start': 4163}], 'id': '1@20KMB_23_210115_H.txt', 'question': '입원/수술/치료 경험 확인'}, {'answers': [{'text': 'A: 흡연하시나요? B: 네 하죠.', 'answer_start': 4205}], 'id': '2@26KMB_23_210115_H.txt', 'question': '흡연 여부'}, {'answers': [{'text': 'A: 음주는 하세요? B: 그럼 하지.', 'answer_start': 4463}], 'id': '3@27KMB_23_210115_H.txt', 'question': '평소 음주 여부'}, {'answers': [{'text': 'A: 지금 어디가 제일 불편하세요? B: 여기 가슴 아래 부분. B: 뭐라 하더라? 아 명치 안쪽이 쓰려요.', 'answer_start': 4617}], 'id': '4@17KMB_23_210115_H.txt', 'question': '통증 부위'}, {'answers': [{'text': 'A: 언제부터 아프셨어요? B: 몰라요. B: 쓰린 거는 최근에야 시작했는데.', 'answer_start': 4707}], 'id': '5@2KMB_23_210115_H.txt', 'question': '주 증상 발생 기간 확인'}, {'answers': [{'text': 'A: 일 점이 가장 약한 통증이고 십 점이 가장 강한 통증일 때 몇 점 정도 되시는가요? B: 근데 이게 계속 아픈 게 아니라 뭐 먹으면 괜찮아지고 그러다가 또 얼마 안 가서 쓰라리고 그래요.', 'answer_start': 4884}], 'id': '6@18KMB_23_210115_H.txt', 'question': '통증 강도'},

In [35]:
import pandas as pd

In [36]:
pd.DataFrame(data)

version                                               data
0    MedQuAD_v1.0_train  {'paragraphs': [{'qas': [{'answers': [{'text':...
1    MedQuAD_v1.0_train  {'paragraphs': [{'qas': [{'answers': [{'text':...
2    MedQuAD_v1.0_train  {'paragraphs': [{'qas': [{'answers': [{'text':...
3    MedQuAD_v1.0_train  {'paragraphs': [{'qas': [{'answers': [{'text':...
4    MedQuAD_v1.0_train  {'paragraphs': [{'qas': [{'answers': [{'text':...
..                  ...                                                ...
330  MedQuAD_v1.0_train  {'paragraphs': [{'qas': [{'answers': [{'text':...
331  MedQuAD_v1.0_train  {'paragraphs': [{'qas': [{'answers': [{'text':...
332  MedQuAD_v1.0_train  {'paragraphs': [{'qas': [{'answers': [{'text':...
333  MedQuAD_v1.0_train  {'paragraphs': [{'qas': [{'answers': [{'text':...
334  MedQuAD_v1.0_train  {'paragraphs': [{'qas': [{'answers': [{'text':...

[335 rows x 2 columns]

In [38]:
import json

In [17]:
data["data"][0]['paragraphs'][0]['qas']

[{'answers': [{'answer_start': 4163,
    'text': 'A: 최근 삼 개월 이내에 입원이나 수술하신 적 있으신가요? B: 아니요.'}],
  'id': '1@20KMB_23_210115_H.txt',
  'question': '입원/수술/치료 경험 확인'},
 {'answers': [{'answer_start': 4205, 'text': 'A: 흡연하시나요? B: 네 하죠.'}],
  'id': '2@26KMB_23_210115_H.txt',
  'question': '흡연 여부'},
 {'answers': [{'answer_start': 4463, 'text': 'A: 음주는 하세요? B: 그럼 하지.'}],
  'id': '3@27KMB_23_210115_H.txt',
  'question': '평소 음주 여부'},
 {'answers': [{'answer_start': 4617,
    'text': 'A: 지금 어디가 제일 불편하세요? B: 여기 가슴 아래 부분. B: 뭐라 하더라? 아 명치 안쪽이 쓰려요.'}],
  'id': '4@17KMB_23_210115_H.txt',
  'question': '통증 부위'},
 {'answers': [{'answer_start': 4707,
    'text': 'A: 언제부터 아프셨어요? B: 몰라요. B: 쓰린 거는 최근에야 시작했는데.'}],
  'id': '5@2KMB_23_210115_H.txt',
  'question': '주 증상 발생 기간 확인'},
 {'answers': [{'answer_start': 4884,
    'text': 'A: 일 점이 가장 약한 통증이고 십 점이 가장 강한 통증일 때 몇 점 정도 되시는가요? B: 근데 이게 계속 아픈 게 아니라 뭐 먹으면 괜찮아지고 그러다가 또 얼마 안 가서 쓰라리고 그래요.'}],
  'id': '6@18KMB_23_210115_H.txt',
  'question': '통증 강도'},
 {'answers': [

In [29]:
data["data"][0]['paragraphs'][0]['qas'][0]

{'answers': [{'answer_start': 4163,
   'text': 'A: 최근 삼 개월 이내에 입원이나 수술하신 적 있으신가요? B: 아니요.'}],
 'id': '1@20KMB_23_210115_H.txt',
 'question': '입원/수술/치료 경험 확인'}

In [23]:
data["data"][0]['paragraphs'][0]['qas'][0]['answers']

[{'answer_start': 4163, 'text': 'A: 최근 삼 개월 이내에 입원이나 수술하신 적 있으신가요? B: 아니요.'}]

In [63]:
def read_data(dir):
    contexts, questions, answers = [], [], []
    
    with open(dir) as data_file:    
        data = json.load(data_file)
        contexts_temp = []
        
    for idx in range(0,334):
        context_temp = data["data"][idx]["paragraphs"][0]["context"]
        context_temp = context_temp.strip()
        contexts.append(context_temp)
        questions.append(data["data"][idx]["paragraphs"][0]["qas"][0]["question"])
        answers.append(data["data"][idx]["paragraphs"][0]["qas"][0]["answers"])
    
    return contexts, questions, answers

In [69]:
train_data = read_data(TRAIN_FILE)

In [70]:
train_contexts, train_questions, train_answers = read_data(TRAIN_FILE)

In [71]:
print('훈련용 상황의 개수 :', len(train_contexts))
print('훈련용 질문의 개수 :',len(train_questions))
print('훈련용 답변의 개수 :',len(train_answers))

훈련용 상황의 개수 : 334
훈련용 질문의 개수 : 334
훈련용 답변의 개수 : 334


In [90]:
train_questions[0]

'입원/수술/치료 경험 확인'

In [98]:
def tokenize(sent):
    return [ x.strip() for x in re.split('(\W+)', sent) if x.strip()]

In [99]:
# Vocabulary 만드는 함수 정의
def preprocess_data(train_data):
    counter = FreqDist()

    # 두 문장의 context를 하나의 문장으로 통합하는 함수
    flatten = lambda data: reduce(lambda x, y: x + y, data)

    # 각 샘플의 길이를 저장하는 리스트
    context_len = []
    question_len = []

    for contexts, questions, answers in [train_data]:
        for context in contexts:
            contexts = tokenize(flatten(context)) # context의 문장들을 펼친 후 토큰화
            context_len.append(len(contexts)) # 각 context의 길이 저장
            for word in contexts: # 단어 집합에 단어 추가
                counter[word] += 1
        for question in questions:
            question = tokenize(question)
            question_len.append(len(question))
            for word in question:
                counter[word] += 1
        for answer in answers:
            answer = tokenize(answer)
            for word in answer:
                counter[word] += 1

    # 단어 집합 생성
    word2idx = {word : (idx + 1) for idx, (word, _) in enumerate(counter.most_common())}
    idx2word = {idx : word for word, idx in word2idx.items()}

    # 가장 긴 샘플의 길이
    context_max_len = np.max(context_len)
    question_max_len = np.max(question_len)

    return word2idx, idx2word, context_max_len, question_max_len

In [100]:
word2idx, idx2word, context_max_len, question_max_len = preprocess_data(train_data)

TypeError: ignored